##  3D Building Models from Volunteered Public Data

**We:**
- **generate Level of Detail 1 (LoD1) 3D Building Models from [OpenStreetMap](https://en.wikipedia.org/wiki/OpenStreetMap) data,**
- **export to [CityJSON](https://www.cityjson.org/) and** 
- **visualize with [pydeck](https://pydeck.gl/index.html).**

In [54]:
#load the magic

%matplotlib inline
import os
from pathlib import Path
import requests

import overpass
import osm2geojson

import numpy as np
import pandas as pd
import geopandas as gpd
from shapely.geometry import Polygon, shape, mapping
import json
import geojson

import ogr

import pydeck as pdk

In [55]:
path = Path('./data')

### Harvest OpenStreetMap

We query the [Overpass API](https://wiki.openstreetmap.org/wiki/Overpass_API) from within [Jupyter](https://jupyter.org/) and covert to [.geojson](https://geojson.org/)  

In [56]:
query = """
[out:json][timeout:25];
// bbox values (minimum latitude, minimum longitude, maximum latitude, maximum longitude)
(
  (
    // I want all buildings
    way[building](-33.522307, 18.456812, -33.500328,  18.487861);

    // plus every building:part
    way["building:part"](-33.522307, 18.456812, -33.500328,  18.487861);
  );
-
  // excluding buildings with relation type=building role=outline
  (
    // for every way in the input set select the relations of which it is an "outline" member
    rel(bw:"outline");
    // back to the ways with role "outline"
    way(r:"outline");
  );
);
out body;
>;
out skel qt;
"""

url = "http://overpass-api.de/api/interpreter"
r = requests.get(url, params={'data': query})
#rr = r.read()
gj = osm2geojson.json2geojson(r.json())

In [1]:
# have a look at a random feature
#gj['features'][1]

### Calculate `height`

We assume a building level is 2.8 meters high and add another 1.3 meters (to account for the roof) and create a new attribute `height`. ~ original script at [hdb3d-code](https://github.com/ualsg/hdb3d-code/blob/master/hdb2d.py).

In [57]:
storeyheight = 2.8

#-- iterate through the list of buildings and create GeoJSON features rich in attributes
footprints = {
    "type": "FeatureCollection",
    "features": []
    }

for i in gj['features']:
    f = {
    "type" : "Feature"
    }
    # at a minimum we only want building:levels tagged
    if 'building:levels' in i['properties']['tags']:
        f["osm_id"] = i['properties']["id"]
        f["properties"] = {}
        
        for p in i["properties"]:
            #-- store all OSM attributes and prefix them with osm_
            f["properties"]["osm_%s" % p] = i["properties"][p]
            osm_shape = shape(i["geometry"])
            #-- a few buildings are not polygons, rather linestrings. This converts them to polygons
            #-- rare, but if not done it breaks the code later
            if osm_shape.type == 'LineString':
                osm_shape = Polygon(osm_shape)
                
                #-- there are also a few multipolygons. We'll take the first one into account. 
                ## -- TODO: make this smarter. 
            elif osm_shape.type == 'MultiPolygon':
                osm_shape = Polygon(osm_shape[0])
                #-- convert the shapely object to geojson
            f["geometry"] = mapping(osm_shape)

    #-- finally calculate the height and store it as an attribute (extrusion of geometry 
    ## -- will be done in the next script)
            f["properties"]['height'] = float(i["properties"]['tags']['building:levels']) * storeyheight + 1.3    
            footprints['features'].append(f)
    
#-- store the data as GeoJSON
with open(path/'mamre_footprints.geojson', 'w') as outfile:
    json.dump(footprints, outfile)

### Reproject to a local coordinate system

The [gdal](https://gdal.org/) [ogr2ogr](https://gdal.org/programs/ogr2ogr.html) program is a swiss-army knife for converting geospatial data and can be executed from jupyter directly. 

In [61]:
!ogr2ogr -f "GeoJSON" \
C:/{entire_path}/mamre_footprints_r.geojson \
C:/{entire_path}/mamre_footprints.geojson \
-s_srs EPSG:4326 -t_srs EPSG:32734

### Extrude

We modify the original [hdb3d.py](https://github.com/ualsg/hdb3d-code/blob/master/hdb3d.py) and execute here.

In [62]:
!python modified_extruder.py

# of features:  7308
done.


#### New semantically rich CityJSON files should be created as per `line 29` of `modified_extruder.py`

CityJSON can be viewed with [azul](https://apps.apple.com/nl/app/azul/id1173239678?mt=12), the [CityJSON QGIS plugin](https://github.com/cityjson/cityjson-qgis-plugin), or the web-viewer [ninja](https://ninja.cityjson.org/).

**We can have a look right here with [pydeck](https://pydeck.gl/index.html); the [deck.gl](https://deck.gl/#/) port for Python.** ~ which gives us the incredible ability to add tooltips.

In [2]:
#footprints['features'][5]

*I want additional visual effects to show the potential and power of 3D City Models; namely: parks, agricultural land and waterways (streams). We get this from OpenStreetMap as well.*

In [63]:
query = """
[out:json][timeout:25];
(
  // query
  way["sport"](-33.522307, 18.456812, -33.500328,  18.487861);
  way['leisure'="park"](-33.522307, 18.456812, -33.500328, 18.487861);
);
// print results
out body;
>;
out skel qt;
"""

url = "http://overpass-api.de/api/interpreter"
p = requests.get(url, params={'data': query})
#rr = r.read()
green_spaces = osm2geojson.json2geojson(p.json())

query = """
[out:json][timeout:25];
(
  // query
  way['landuse'='farmland'](-33.522307, 18.456812, -33.500328, 18.487861);
);
// print results
out body;
>;
out skel qt;
"""

url = "http://overpass-api.de/api/interpreter"
fl = requests.get(url, params={'data': query})
#rr = r.read()
farm_spaces = osm2geojson.json2geojson(fl.json())

query = """
[out:json][timeout:25];
(
  // query
  way['waterway'='stream'](-33.522307, 18.456812, -33.500328, 18.487861);
);
// print results
out body;
>;
out skel qt;
"""

url = "http://overpass-api.de/api/interpreter"
w = requests.get(url, params={'data': query})
#rr = r.read()
stream = osm2geojson.json2geojson(w.json())

#-- store the data to GeoJSON * as desired
#with open(path/'{.....filenamehere....}.geojson', 'w') as outfile:
    #json.dump({...inputfilenamehere...}}, outfile)

In [3]:
#green_spaces["features"][8]

#### I experienced challenges with geojson and was forced to convert to pandas.

In [64]:
data = './data/mamre_footprints.geojson'
json = pd.read_json(data)
build_df = pd.DataFrame()

In [65]:
# have a look at a random feature
#json['features'][18]['properties']

##### pydeck needs an area and a center
~ In order to make the most of the semantic data we need to extract the `osm_tags` from the dictionary: this can be any data you have.

In [67]:
bbox = [(18.456812, -33.522307), (18.456812, -33.500328), 
        (18.497861, -33.500328), (18.496812, -33.522307)]
y = -33.5123
x = 18.4700

In [69]:
# Parse the geometry out to Pandas
build_df["coordinates"] = json["features"].apply(lambda row: row["geometry"]["coordinates"])
#build_df["height"] = round(json["features"].apply(lambda row: row["properties"]["height"]), 1)

#we want to extract values from the dictionary 
build_df["tags"] = json["features"].apply(lambda row: row["properties"]["osm_tags"])
build_df['level'] = build_df['tags'].apply(lambda x: x.get('building:levels'))
build_df['city'] = build_df['tags'].apply(lambda x: x.get('addr:city'))
build_df['street'] = build_df['tags'].apply(lambda x: x.get('addr:street'))
build_df['type'] = build_df['tags'].apply(lambda x: x.get('building'))

In [16]:
#build_df["tags"][0]

In [70]:
## ~ (x, y) - bl, tl, tr, br  ~~ or ~~ sw, nw, ne, se
area = [[[bbox[0][0], bbox[0][1]], [bbox[1][0], bbox[1][1]], 
         [bbox[2][0], bbox[2][1]], [bbox[3][0], bbox[3][1]]]]

## ~ (y, x)
view_state = pdk.ViewState(latitude=y, longitude=x, zoom=14.5, max_zoom=19, pitch=65, 
                                   bearing=65)

polygon = pdk.Layer(
    "PolygonLayer",
    area,
    stroked=False,
    # processes the data as a flat longitude-latitude pair
    get_polygon="-",
    get_fill_color=[0, 0, 0, 0],
)

building_layer = pdk.Layer(
    "PolygonLayer",
    build_df,
    #id="geojson",
    opacity=0.6,
    stroked=False,
    get_polygon="coordinates",
    filled=True,
    extruded=True,
    wireframe=True,
    get_elevation="height",
    get_fill_color="[192,192,192]", #255, 255, 255]",
    get_line_color=[192,192,192], #[255, 255, 255],
    auto_highlight=True,
    pickable=True,
)

greenspaces_layer =  pdk.Layer(
    "GeoJsonLayer",
    green_spaces,
    opacity=0.5,
    stroked=False,
    filled=True,
    wireframe=True,
    get_fill_color="[14, 140, 58]",
    get_line_color='[14, 140, 58]',
)

farm_layer =  pdk.Layer(
    "GeoJsonLayer",
    farm_spaces,
    opacity=0.4,
    stroked=False,
    filled=True,
    wireframe=True,
    get_fill_color="[170, 83, 3]",
    get_line_color='[170, 83, 3]',
)

water_layer =  pdk.Layer(
    "GeoJsonLayer",
    stream,
    opacity=0.8,
    stroked=False,
    filled=True,
    wireframe=True,
    get_fill_color="[35, 35, 142]",
    get_line_color='[35, 35, 142]',
)

tooltip = {"html": "<b>Levels:</b> {level} <br/> <b>Addres:</b> {street}, {city}\
<br/> <b>Building Type:</b> {type}"}
          
r = pdk.Deck(layers=[polygon, building_layer, greenspaces_layer, farm_layer, water_layer], 
             #views=[{"@@type": "MapView", "controller": True}],
             initial_view_state=view_state,
             map_style='dark',
             tooltip=tooltip)

#save
r.to_html("./img/mamre.html")

**on a laptop without a mouse:**
- trackpad `left-click drag-left` and `-right`,
- `Ctrl left-click drag-up`, `-down`, `-left` and `-right` to rotate and so-on and
- `+` next to `Backspace` zoom-in and `-` next to `+` zoom-out.

**Now you do your community.** *~ If your area lacks OpenStreetMap data and you want to contribute please follow the [Guide](https://wiki.openstreetmap.org/wiki/Beginners%27_guide).*